In [1]:
import pybliometrics.scopus as scopus
import numpy as np
import pandas as pd
import random
import time

In [2]:
seed = 7 # seed for NMF topic model
num_topics = 12
query = 'title-abs-key("engineering" AND "research" AND "innovation") AND PUBYEAR = 2023'
labels = 'ABCDEFGHIJKLMNOPQRSTUVWXYZ'
vis_seed = 6 # seed for t-SNE visualization
vis_angle = 135 # rotation angle for visualization

In [3]:
scopus.init()
papers = scopus.ScopusSearch(query, subscriber=True, verbose=True)
print(papers.results)

[Document(eid='2-s2.0-85198701893', doi='10.3973/j.issn.2096-4498.2023.S2.002', pii=None, pubmed_id=None, title='Achievements and Prospects of Yunnan Highway Tunnel Construction', subtype='ar', subtypeDescription='Article', creator='Li G.', afid='126665626;126298775', affilname='Ltd.;Ltd.', affiliation_city='Kunming;Kunming', affiliation_country='China;China', author_count='2', author_names='Li, Guofeng;Li, Zhihou', author_ids='55714056900;36066042300', author_afids='126665626;126298775', coverDate='2023-12-30', coverDisplayDate='30 December 2023', publicationName='Tunnel Construction', issn='20964498', source_id='21101089370', eIssn=None, aggregationType='Journal', volume='43', issueIdentifier=None, article_number=None, pageRange='10-26', description='To promote the popularization and application of engineering technology and innovation achievements in the construction of highway tunnels in Yunnan province, China, the achievements in the construction of highway tunnels in Yunnan in th

In [18]:
df = pd.DataFrame(papers.results)

In [4]:
# สร้าง DataFrame เพื่อบันทึกเป็น CSV
data = []

for paper in papers.results:
    # Format the author names
    if hasattr(paper, 'author_names') and paper.author_names:
        # Split the author names by ';' and remove leading/trailing spaces
        authors = paper.author_names.split(';')
        authors = [author.strip() for author in authors]  # Strip extra spaces

        formatted_authors = []
        for author in authors:
            name_parts = author.split(',')
            if len(name_parts) == 2:  # If the name has both Lastname and Firstname
                last_name = name_parts[0].strip()
                first_name = name_parts[1].strip()
                # Only append the initial if there is a first name
                if first_name:
                    formatted_authors.append(f"{last_name} {first_name[0]}.")
                else:
                    formatted_authors.append(f"{last_name}.")  # In case of missing first name
            else:  # If the name is a single part (like just Lastname)
                formatted_authors.append(f"{name_parts[0].strip()}.")

        # Join formatted authors with "; "
        formatted_authors = "; ".join(formatted_authors)
    else:
        formatted_authors = ""

    paper_dict = {
        "Title": paper.title,
        "Abstract": paper.description if hasattr(paper, 'description') else "",
        "Author": formatted_authors,
        "Aggregation_Type": paper.aggregationType if hasattr(paper, 'aggregationType') else "",
        "Publisher": paper.publicationName if hasattr(paper, 'publicationName') else "",
        "Publication_Date": paper.coverDate if hasattr(paper, 'coverDate') else "",
        "Institutions": "; ".join(paper.affilname.split('; ')) if hasattr(paper, 'affilname') and paper.affilname else "",
        "Keywords": "; ".join(paper.authkeywords.split('|')) if hasattr(paper, 'authkeywords') and paper.authkeywords else "",
    }
    data.append(paper_dict)



df = pd.DataFrame(data)

output_file = "scopus_papers_2023_full_details.csv"
df.to_csv(output_file, index=False, encoding="utf-8")